In [1]:
import pandas as pd
from matplotlib import pyplot as plt
from matplotlib.animation import FuncAnimation
import cartopy.crs as ccrs
from cartopy.feature import NaturalEarthFeature
import cartopy.feature as cfeature
import xarray as xr
import numpy as np
from urllib.request import urlopen
import json
import os
from netCDF4 import Dataset
import requests
import h5py
import os
import altair as alt
from vega_datasets import data
from altair import datum

In [34]:
df = pd.read_csv('indicatorsByCountryFinal.csv', sep='\t')

In [37]:
dffif = df[df['year'] == 1950]

In [45]:
df[df['country'] == 'India']['soiltemp']

7171    293.20890
7172    293.47180
7173    293.72357
7174    293.42374
7175    293.66763
          ...    
7267    296.58210
7268    296.70490
7269    297.49893
7270    297.11322
7271    297.05014
Name: soiltemp, Length: 101, dtype: float64

In [48]:
for i in range(len(df)):
    df['soiltemp'][i] = df['soiltemp'][i] - dffif[dffif['country'] == df['country'][i]]['soiltemp']

/var/folders/h_/gldyz8dx31v7h1hxx4h6f8g40000gn/T/ipykernel_63987/3342593903.py:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df['soiltemp'][i] = df['soiltemp'][i] - dffif[dffif['country'] == df['country'][i]]['soiltemp']


In [68]:
df

country  country-code  region-code  sub-region-code  year  \
0        Afghanistan             4        142.0             34.0  1950   
1        Afghanistan             4        142.0             34.0  1951   
2        Afghanistan             4        142.0             34.0  1952   
3        Afghanistan             4        142.0             34.0  1953   
4        Afghanistan             4        142.0             34.0  1954   
...              ...           ...          ...              ...   ...   
18680  Åland Islands           248        150.0            154.0  2046   
18681  Åland Islands           248        150.0            154.0  2047   
18682  Åland Islands           248        150.0            154.0  2048   
18683  Åland Islands           248        150.0            154.0  2049   
18684  Åland Islands           248        150.0            154.0  2050   

       soiltemp  surfacetempanomaly  precipitationflux  
0       0.00000           287.41458           0.000019  
1       0.14850           287.38846           0.000015  
2       0.67294           287.35420           0.000012  
3       0.71956           286.78772           0.000012  
4       0.51483           287.79840           0.000012  
...         ...                 ...                ...  
18680   1.08272           271.81415           0.000034  
18681   2.52562           273.41702           0.000046  
18682   3.02440           273.15576           0.000037  
18683   2.52995           274.32970           0.000040  
18684   2.99270           273.14926           0.000041  

[18685 rows x 8 columns]

In [60]:
max(df['soiltemp'])

5.875249999999994

In [66]:
# df = df[df['year'] >= 2045]
alt.data_transformers.disable_max_rows()

def timestamp(t):
    return pd.to_datetime(t)

countries = alt.topo_feature(data.world_110m.url, 'countries')

slider = alt.binding_range(
    step=1,
    min=df['year'].min(), 
    max=df['year'].max()
)

select_date = alt.selection_single(
    name="slider", 
    fields=['year'],
    bind=slider, 
)

alt.Chart(countries).mark_geoshape()\
    .encode(color='rate:Q')\
    .add_selection(select_date)\
    .transform_filter(select_date)\
    .transform_lookup(
        lookup='id',
        from_=alt.LookupData(df, key='country-code', fields=['soiltemp'])
    )\
    .project('equirectangular')\
    .properties(
        width=500,
        height=300,
        title='Title'
    )

alt.Chart(df).mark_geoshape()\
    .encode(color=alt.Color('soiltemp:Q', scale=alt.Scale(domain=[-6, 6], scheme='blueorange')))\
    .add_selection(select_date)\
    .transform_filter(select_date)\
    .transform_lookup(
        lookup='country-code',
        from_=alt.LookupData(countries, key='id',
                             fields=["type", "properties", "geometry"])
    )\
    .project('equalEarth')\
    .properties(
        width=500,
        height=300,
        title='Title'
    )

alt.Chart(...)

In [74]:
import altair as alt
from vega_datasets import data

alt.Chart(df).mark_line(point=True)\
    .encode(
        alt.X('soiltemp', scale=alt.Scale(zero=False)),
        alt.Y('precipitationflux', scale=alt.Scale(zero=False)),
        order=['year'],
        color=alt.Color('country'))\
    .properties(
        width=500,
        height=300,
        title='Title'
    )

alt.Chart(...)

In [ ]:
import altair as alt
from vega_datasets import data

source = data.driving()

alt.Chart(source).mark_line(point=True).encode(
    alt.X('soiltemp', scale=alt.Scale(zero=False)),
    alt.Y('gas', scale=alt.Scale(zero=False)),
    order='year'
)